<img style="display: block; margin: auto; width: 50%;" src="https://ctapipe.readthedocs.io/en/latest/_images/ctapipe_logo.webp">
<p style="text-align: center; font-size: 3.5rem">
IO: TableLoader and EventSource(s) 
</p>

`ctapipe` provides basically two different ways of accessing its data products:
 - event-wise (***EventSource***)
 - column-wise (***TableLoader***)

### EventSource(s):
EventSources read input files and generate `ctapipe.containers.ArrayEventContainer`
instances when iterated over.

A new EventSource should be created for each type of event file read
into ctapipe, e.g. simtel files are read by the `ctapipe.io.SimTelEventSource`.

EventSource provides a common high-level interface for accessing event
information from different data sources. Creating an EventSource for a new
file format or other event source ensures that data can be accessed in a common way,
irregardless of the file format or data origin.

EventSource itself is an abstract class, but will create an
appropriate subclass if a compatible source is found for the given
`input_url`.

### TableLoader:
Loads telescope-event or subarray-event data from ctapipe HDF5 files and returns `astropy.table`.
See [Astropy docs](https://docs.astropy.org/en/stable/table/) or [this repo from the 2022 ESCAPE School](https://github.com/escape2020/school2022/tree/main/astropy)

This class provides high-level access to data stored in ctapipe HDF5 files,
such as created by the ctapipe-process tool (`ctapipe.tools.process.ProcessorTool`).

There are multiple `TableLoader` methods loading data from all relevant tables,
depending on the options, and joins them into single tables:

 - `TableLoader.read_subarray_events`
 - `TableLoader.read_telescope_events`
 - `TableLoader.read_telescope_events_by_id`
 - `TableLoader.read_telescope_events_by_type`


The last one returns a dict with a table per telescope type, which is needed for e.g. DL1 image data that might have
different shapes for each of the telescope types as tables do not support variable length columns.

----
----

## EventSource:

In [1]:
from ctapipe.io import EventSource, DataWriter
from ctapipe import utils
from traitlets.config import Config

In [2]:
! rm -rf ./build
! mkdir ./build

In [3]:
# simtel.zst file
test_data_path = "/home/jonas/repos/2023-10-datapipe-workshop-material/data/datapipe_workshop/simtel/"
simtel_path = test_data_path + "gamma_20deg_0deg_run1000___cta-prod5b-lapalma_desert-2158m-LaPalma-dark_cone10.simtel.zst"
# simtel_path = utils.get_dataset_path("gamma_prod5.simtel.zst")

# create dummy r1 file from ./create_dummy_data.ipynb // needs ctapipe_io_lst
%run ./create_dummy_data.ipynb
dummy_r1_path = "./build/LST-1.1.Run10000.0000.fits.fz"

2023-10-26T09:03:41 - Will compress data sequentially
2023-10-26T09:03:41 - Will compress data sequentially
2023-10-26T09:03:41 - Will compress data sequentially
2023-10-26T09:03:41 - Will compress data sequentially
2023-10-26T09:04:03 - Closed  ./build/LST-1.4.Run10000.0000.fits.fz
2023-10-26T09:04:03 - Closed  ./build/LST-1.3.Run10000.0000.fits.fz
2023-10-26T09:04:03 - Closed  ./build/LST-1.2.Run10000.0000.fits.fz
2023-10-26T09:04:03 - Closed  ./build/LST-1.1.Run10000.0000.fits.fz


`EventSource` will create an appropriate subclass if a compatible source is found for the given `input_url`:


In [4]:
! ctapipe-info --event-sources


*** ctapipe available EventSource implementations ***

  HDF5EventSource -- ctapipe.io.hdf5eventsource.HDF5EventSource
SimTelEventSource -- ctapipe.io.simteleventsource.SimTelEventSource
   LSTEventSource -- ctapipe_io_lst.LSTEventSource


In [5]:
# Needs ctapipe_io_lst
source = EventSource(input_url=dummy_r1_path, max_events=5)
print(source) # LSTEventSource
source

In [6]:
source = EventSource(input_url=simtel_path, max_events=5)
print(source) # SimtTelEventSource
source

In [7]:
for event in source:
    print(event.count)

0
1
2
3
4


Generates `ctapipe.containers.ArrayEventContainer`. See [API Documentation](https://ctapipe.readthedocs.io/en/latest/api/ctapipe.containers.ArrayEventContainer.html#ctapipe.containers.ArrayEventContainer).

In [8]:
event

ctapipe.containers.ArrayEventContainer:
                       index.*: event indexing information with default None
                          r0.*: Raw Data with default None
                          r1.*: R1 Calibrated Data with default None
                         dl0.*: DL0 Data Volume Reduced Data with default None
                         dl1.*: DL1 Calibrated image with default None
                         dl2.*: DL2 reconstruction info with default None
                  simulation.*: Simulated Event Information with default None
                                with type <class
                                'ctapipe.containers.SimulatedEventContainer'>
                     trigger.*: central trigger information with default None
                         count: number of events processed with default 0
                    pointing.*: Array and telescope pointing positions with
                                default None
                 calibration.*: Container for calibra

 - Every time a new loop is started through the source,
it tries to restart from the first event, which might not be supported
by the event source. It is encouraged to use ``EventSource`` in a **context manager** to ensure
the correct cleanups are performed when you are finished with the source:

In [9]:
with EventSource(input_url=simtel_path, max_events=5) as source:
    for event in source:
        print(f"Event Count: {event.count}, Tels with trigger: {event.trigger.tels_with_trigger}")

Event Count: 0, Tels with trigger: [16 31 32]
Event Count: 1, Tels with trigger: [ 1  2 17 32]
Event Count: 2, Tels with trigger: [30 36 49]
Event Count: 3, Tels with trigger: [ 1  4  6  7  8 19 21 22 23 34 40 53 61 63 64 65 68 71 76 77]
Event Count: 4, Tels with trigger: [15 30 36 49 75 84]


 - You can hand in the Ids of the telescopes to be included in the data with the `allowed_tels` attribute. If given, only this subset of telescopes will be present in the generated events. If None, all available telescopes are used.

In [10]:
eventsource_config = Config(
    {
        "EventSource": {
            "max_events": 5,
            "allowed_tels" : [3, 4, 9]
        }
    }
)

In [11]:
with EventSource(input_url=simtel_path, config=eventsource_config) as source:
    for event in source:
        print(f"Event Count: {event.count}, Tels with trigger: {event.trigger.tels_with_trigger}")

Event Count: 0, Tels with trigger: [4]
Event Count: 1, Tels with trigger: [4]
Event Count: 2, Tels with trigger: [3]
Event Count: 3, Tels with trigger: [3 4]
Event Count: 4, Tels with trigger: [9]


 - E.g. calibrate your data in the event loop and write it to an .h5 file with the `DataWriter`:

In [12]:
from ctapipe.calib import CameraCalibrator

source = EventSource(input_url=simtel_path, max_events=50)
calibrate = CameraCalibrator(subarray=source.subarray)

with DataWriter(event_source=source, output_path="build/events.dl1.h5", write_parameters=False, overwrite=True, write_images=True) as write_data:
    for event in source:
        calibrate(event)
        write_data(event)

In [13]:
! ctapipe-process -i {simtel_path} -o ./build/events.dl1.h5 --overwrite --progress

2023-10-26 11:04:15,988 WARNING [ctapipe.ctapipe-process.DataWriter] (datawriter._setup_output_path): Overwriting /home/jonas/repos/2023-10-datapipe-workshop-material/tableloader_api/build/events.dl1.h5
2023-10-26 11:04:16,631 WARNING [ctapipe.core.telescope_component] (telescope_component.attach_subarray): TelescopeParameter type argument 'SST_1M_*' did not match any known telescope types
SimTelEventSource: 1054ev [00:55, 19.02ev/s]


## TableLoader:

In [14]:
from ctapipe.io import TableLoader

In [15]:
dl1_h5_file = "./build/events.dl1.h5"

In [16]:
loader = TableLoader(
    input_url=dl1_h5_file, 
    load_dl1_images=True,
    load_dl1_parameters=False,
    load_dl1_muons=False,
    load_dl2=False,
    load_simulated=False,
    load_true_images=True,
    load_true_parameters=False,
    load_instrument=True,
)

 - Or with a config file:

In [17]:
tableloader_config = Config(
    {
        "TableLoader": {
            "input_url": "./build/events.dl1.h5",
            "load_dl1_images": True,
            "load_dl1_parameters": False,
            "load_dl1_muons": False,
            "load_dl2": False,
            "load_simulated": False,
            "load_true_images": True,
            "load_true_parameters": False,
            "load_instrument": True,
            }
    }
)

loader = TableLoader(config=tableloader_config)

 - Reading subarray-based event information:

In [18]:
subarray_events = loader.read_subarray_events(start=None, stop=None)
subarray_events

<Table length=1054>
obs_id event_id        time        tels_with_trigger event_type
int32   int64          Time             bool[84]       int64   
------ -------- ------------------ ----------------- ----------
  1000    19514 59177.969306676714    False .. False         32
  1000    21412   59177.9695935642     True .. False         32
  1000    29308  59177.97034592544    False .. False         32
  1000    34807  59177.97078015721     True .. False         32
  1000    34815  59177.97097334443     False .. True         32
  1000    40109  59177.97119783291     False .. True         32
  1000    40111  59177.97133508081    False .. False         32
  1000    43400  59177.97183612266    False .. False         32
  1000    43408  59177.97194710433    False .. False         32
  1000    43417  59177.97206856716    False .. False         32
  1000    53306  59177.97239660824    False .. False         32
  1000    53313  59177.97255197875     True .. False         32
  1000    78606   59177.9733437246    False .. False         32
  1000    79600  59177.97341557817    False .. False         32
  1000    79604  59177.97353212917    False .. False         32
  1000    79618 59177.973672001805    False .. False         32
  1000    98400  59177.97436385388     False .. True         32
  1000    98403  59177.97445015003    False .. False         32
  1000    98405  59177.97455913149    False .. False         32
  1000    98417 59177.974794261216    False .. False         32
  1000    98705 59177.975286369074    False .. False         32
   ...      ...                ...               ...        ...
  1000  4890612  59178.39771484337     False .. True         32
  1000  4901001  59178.39824026565    False .. False         32
  1000  4901015 59178.398347596056    False .. False         32
  1000  4901301 59178.398460971744    False .. False         32
  1000  4901303 59178.398527967525    False .. False         32
  1000  4901308 59178.398739174736    False .. False         32
  1000  4906311  59178.39924090825    False .. False         32
  1000  4906314  59178.39928329973    False .. False         32
  1000  4907103  59178.39945733733    False .. False         32
  1000  4907111 59178.399609725915    False .. False         32
  1000  4907117 59178.399770255346    False .. False         32
  1000  4908610  59178.40014502259    False .. False         32
  1000  4919602   59178.4011451733    False .. False         32
  1000  4919611  59178.40128569603    False .. False         32
  1000  4920415  59178.40154388048    False .. False         32
  1000  4923916  59178.40164320538    False .. False         32
  1000  4956701  59178.40390698793    False .. False         32
  1000  4958803    59178.404233055    False .. False         32
  1000  4958813  59178.40429469844    False .. False         32
  1000  4977301  59178.40464983339    False .. False         32
  1000  4991405  59178.40515629595    False .. False         32
  1000  4998318  59178.40911587855    False .. False         32

 - in chunks:

In [19]:
subarray_events_chunked = loader.read_subarray_events_chunked(chunk_size=500)
subarray_events_chunked

In [20]:
for chunk in subarray_events_chunked:
    print(chunk)

Chunk(start=0, stop=500, data=<Table length=500>
obs_id event_id        time        tels_with_trigger event_type
int32   int64          Time             bool[84]       int64   
------ -------- ------------------ ----------------- ----------
  1000    19514 59177.969306676714    False .. False         32
  1000    21412   59177.9695935642     True .. False         32
  1000    29308  59177.97034592544    False .. False         32
  1000    34807  59177.97078015721     True .. False         32
  1000    34815  59177.97097334443     False .. True         32
  1000    40109  59177.97119783291     False .. True         32
  1000    40111  59177.97133508081    False .. False         32
  1000    43400  59177.97183612266    False .. False         32
  1000    43408  59177.97194710433    False .. False         32
  1000    43417  59177.97206856716    False .. False         32
  1000    53306  59177.97239660824    False .. False         32
  1000    53313  59177.97255197875     True .. False   

 - read just LST events:

In [21]:
LST_events = loader.read_telescope_events(telescopes=[1, 2, 3, 4])
LST_events

<Table length=463>
obs_id event_id tel_id     time_mono      ...        time        tels_with_trigger event_type
                                          ...                                                
int32   int64   int16         Time        ...        Time             bool[84]       int64   
------ -------- ------ ------------------ ... ------------------ ----------------- ----------
  1000    21412      1   59177.9695935642 ...   59177.9695935642     True .. False         32
  1000    21412      2   59177.9695935642 ...   59177.9695935642     True .. False         32
  1000    34807      1  59177.97078015721 ...  59177.97078015721     True .. False         32
  1000    34807      4  59177.97078015721 ...  59177.97078015721     True .. False         32
  1000    53313      1  59177.97255197875 ...  59177.97255197875     True .. False         32
  1000    53313      4  59177.97255197875 ...  59177.97255197875     True .. False         32
  1000    98705      2 59177.975286369074 ... 59177.975286369074    False .. False         32
  1000    98705      3 59177.975286369074 ... 59177.975286369074    False .. False         32
  1000   118305      1  59177.97652243004 ...  59177.97652243004     True .. False         32
  1000   118305      2  59177.97652243005 ...  59177.97652243004     True .. False         32
  1000   118305      3  59177.97652243005 ...  59177.97652243004     True .. False         32
  1000   118305      4  59177.97652243004 ...  59177.97652243004     True .. False         32
  1000   163203      1  59177.98144993602 ...  59177.98144993602     True .. False         32
  1000   163203      2  59177.98144993602 ...  59177.98144993602     True .. False         32
  1000   163203      3  59177.98144993602 ...  59177.98144993602     True .. False         32
  1000   163203      4  59177.98144993602 ...  59177.98144993602     True .. False         32
  1000   182713      1 59177.983494839886 ... 59177.983494839886     True .. False         32
  1000   182713      2 59177.983494839886 ... 59177.983494839886     True .. False         32
  1000   182713      3 59177.983494839886 ... 59177.983494839886     True .. False         32
  1000   182713      4 59177.983494839886 ... 59177.983494839886     True .. False         32
  1000   240303      2  59177.98773430978 ...  59177.98773430978    False .. False         32
   ...      ...    ...                ... ...                ...               ...        ...
  1000  4514514      1   59178.3709096196 ...   59178.3709096196     True .. False         32
  1000  4514514      2   59178.3709096196 ...   59178.3709096196     True .. False         32
  1000  4514514      3   59178.3709096196 ...   59178.3709096196     True .. False         32
  1000  4550714      1 59178.376479723716 ... 59178.376479723716     True .. False         32
  1000  4550714      3 59178.376479723716 ... 59178.376479723716     True .. False         32
  1000  4550714      4 59178.376479723716 ... 59178.376479723716     True .. False         32
  1000  4598714      2   59178.3792407076 ...   59178.3792407076    False .. False         32
  1000  4598714      3   59178.3792407076 ...   59178.3792407076    False .. False         32
  1000  4598714      4   59178.3792407076 ...   59178.3792407076    False .. False         32
  1000  4717915      1  59178.38494373778 ...  59178.38494373778     True .. False         32
  1000  4717915      2  59178.38494373778 ...  59178.38494373778     True .. False         32
  1000  4877617      1 59178.392777976274 ... 59178.392777976274     True .. False         32
  1000  4877617      2 59178.392777976274 ... 59178.392777976274     True .. False         32
  1000  4882910      1  59178.39594072801 ...  59178.39594072801      True .. True         32
  1000  4882910      4  59178.39594072801 ...  59178.39594072801      True .. True         32
  1000  4888608      1 59178.397167374605 ... 59178.397167374605     True .. False         32
  1000  4888608      2 59178.3971

 - Loads telescope events by type
 - returns dict with different telescope types

In [22]:
telescope_events_by_type = loader.read_telescope_events_by_type(telescopes=["LST_LST_LSTCam", "MST_MST_FlashCam"])
telescope_events_by_type

{'LST_LST_LSTCam': <Table length=463>
 obs_id event_id tel_id     time_mono      ...        time        tels_with_trigger event_type
                                           ...                                                
 int32   int64   int16         Time        ...        Time             bool[84]       int64   
 ------ -------- ------ ------------------ ... ------------------ ----------------- ----------
   1000    21412      1   59177.9695935642 ...   59177.9695935642     True .. False         32
   1000    21412      2   59177.9695935642 ...   59177.9695935642     True .. False         32
   1000    34807      1  59177.97078015721 ...  59177.97078015721     True .. False         32
   1000    34807      4  59177.97078015721 ...  59177.97078015721     True .. False         32
   1000    53313      1  59177.97255197875 ...  59177.97255197875     True .. False         32
   1000    53313      4  59177.97255197875 ...  59177.97255197875     True .. False         32
   1000    9

 - reads telescope events by ID
 - returns dict of telescope ID's

In [23]:
telescope_events_by_id = loader.read_telescope_events_by_id(telescopes=[1, 2])
telescope_events_by_id

{1: <Table length=108>
 obs_id event_id tel_id     time_mono      ...        time        tels_with_trigger event_type
                                           ...                                                
 int32   int64   int16         Time        ...        Time             bool[84]       int64   
 ------ -------- ------ ------------------ ... ------------------ ----------------- ----------
   1000    21412      1   59177.9695935642 ...   59177.9695935642     True .. False         32
   1000    34807      1  59177.97078015721 ...  59177.97078015721     True .. False         32
   1000    53313      1  59177.97255197875 ...  59177.97255197875     True .. False         32
   1000   118305      1  59177.97652243004 ...  59177.97652243004     True .. False         32
   1000   163203      1  59177.98144993602 ...  59177.98144993602     True .. False         32
   1000   182713      1 59177.983494839886 ... 59177.983494839886     True .. False         32
   1000   251006      1 591

 - `read_telescope_events_chunked`, `read_telescope_events_by_type_chunked` and `read_telescope_events_by_id_chunked` are also available 

In [24]:
simulation_configuration = loader.read_simulation_configuration()
shower_distribution = loader.read_shower_distribution() #
observation_information = loader.read_observation_information()

In [25]:
simulation_configuration

<Table length=1>
obs_id corsika_version simtel_version ... corsika_wlen_max corsika_low_E_detail corsika_high_E_detail
                                      ...        nm                                                  
int32       int64          int64      ...     float64             int64                 int64        
------ --------------- -------------- ... ---------------- -------------------- ---------------------
  1000            7710     1593349643 ...            900.0                    0                   303

In [26]:
shower_distribution

<Table length=1>
obs_id hist_id n_entries   bins_energy   bins_core_dist    histogram    
                               TeV             m                        
int32   int64    int64     float64[121]   float64[201]  float32[120,200]
------ ------- --------- --------------- -------------- ----------------
  1000       6   1000000 0.001 .. 1000.0  0.0 .. 3800.0       0.0 .. 0.0

In [27]:
observation_information

<Table length=1>
obs_id sb_id  producer_id state ... scheduled_start_time actual_start_time actual_duration
                                ...                                              min      
uint64 uint64    str10    int64 ...         Time                Time           float64    
------ ------ ----------- ----- ... -------------------- ----------------- ---------------
  1000   1000  simulation     1 ...    59177.96810185185 59177.96810185185             nan

Now you have `astropy.table`s including all the relevant data you need for your analyses.

### Example

You want to analyze your brand new image cleaning algorithm on LST images:

In [28]:
from astropy.table import Table

In [29]:
# with EventSource
def ES(input_url):
    table = Table()
    images = []
    with EventSource(input_url=input_url, allowed_tels=[1, 2, 3, 4]) as source:
        for event in source:
            tel = event.dl1.tel
            for tel_id in tel.keys():
                images.append(tel[tel_id].image)
    table['image'] = images
    return images

In [30]:
# with TableLoader
def TL(input_url):
    loader = TableLoader(
        input_url=input_url, 
        load_dl1_images=True,
        load_true_images=True,
    )
    tel_events = loader.read_telescope_events(telescopes=[1, 2, 3, 4])

    return tel_events

In [31]:
%timeit ES(dl1_h5_file)
%timeit TL(dl1_h5_file)

2.67 s ± 13.7 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
130 ms ± 733 µs per loop (mean ± std. dev. of 7 runs, 10 loops each)
